In [ ]:
import numpy as np
import gzip
import pickle
from scipy.stats import rankdata
import collections
import matplotlib.pyplot as plt

%matplotlib inline

## Classificateur de type k-NN et représentants moyens

L'objectif de ce TP est d'implémenter des classificateurs de type k plus proches voisins et représentants moyens. C'est aussi l'occasion de se familiariser avec numpy.

Nous utiliserons le jeu de données MNIST. L'objectif est de prédire le chiffre contenu sur une image (entre 0 et 9).

Commencer par télécharger le jeu de données (cherchez "mnist.pkl.gz" sur google, il peut se trouver par exemple ici : https://github.com/mnielsen/neural-networks-and-deep-learning/blob/master/data/mnist.pkl.gz )


In [ ]:
f = gzip.open('/Users/corro/notebook/proba_alternance/new/mnist.pkl.gz', 'rb')
u = pickle._Unpickler(f)
u.encoding = 'latin1'
train_set, dev_set, test_set = u.load()

X_train, Y_train = train_set
X_dev, Y_dev = dev_set
X_test, Y_test = test_set

print(X_train.shape, Y_train.shape)

# just keep the 5000 or 500 first ones, because we want this to be fast
X_train = X_train[:5000]
Y_train = Y_train[:5000]
X_test = X_test[:500]
Y_test = Y_test[:500]
X_dev = X_dev[:500]
Y_dev = Y_dev[:500]
print(X_test.shape, Y_test.shape)

In [ ]:
# Affiche la 1ere image des données d'entrainement
print("First image contains a: ", Y_train[0])
plt.imshow(X_train[0].reshape(28, 28))

In [ ]:
# on peut facilement récupérer une seule image

x = X_test[0]
y = Y_test[0]

print(x.shape, y.shape, y)

## Classificateur plus proche voisin

On commence par le classificateur le plus simple : pour prédire le chiffre sur une image, on cherche l'image la "plus proche" (en terme de distance euclidienne) dans les données d'entrainement. et on retourne le chiffre sur cette dernière. Ici, l'entrainement consiste simplement à enregistrer toutes les données d'entrainement.

Que peut-on déduire des résultats ?

In [ ]:
# examples d'utilisation de la fonction argmin

w = np.random.rand(3)
print(w)
print(w.argmin())
print()

w = np.random.rand(2, 3)
print(w)
print(w.argmin(axis=1))

In [ ]:
class NNClassifier:
    # dans le constructeur, on copie simplement les données d'entrainement
    def __init__(self, X_train, Y_train):
        self.X_train = X_train
        self.Y_train = Y_train
        
    # prédit le chiffre sur l'image x
    # en cherchant l'image la plus proche dans X_train
    def predict(self, x):
        assert len(x.shape) == 1
        assert x.shape[0] == self.X_train.shape[1]
        
        # TODO TODO
    
    # Calcul la précision du classificateur sur les données X, Y
    def accuracy(self, X, Y):
        assert len(X.shape) == 2
        assert len(Y.shape) == 1
        assert X.shape[1] == self.X_train.shape[1]
        assert X.shape[0] == Y.shape[0]

        # TODO TODO

In [ ]:
# construit le classificateur et calcul la précision sur les données de test
classifier = NNClassifier(X_train, Y_train)
classifier.accuracy(X_test, Y_test)

In [ ]:
# on peut aussi calculer la précision sur les données d'entrainement.
classifier.accuracy(X_train[:500], Y_train[:500])

## Classificateur k plus proche voisin

Maintenant, plutôt que de prédire le chiffre sur l'image la plus proche dans les données d'entrainement, on va chercher les k images les plus proches et prédire le chiffre le plus présent dans celles ci. Pour cela, vous pouvez utiliser la class collections.Counter.

Que peut-on déduire des résultats ?

In [ ]:
# pour trouver les positions des k plus petites valeurs d'un vecteur
k = 2
distances = np.array([4., 3., 6., 10., 2.])
np.argpartition(distances, k)[:k]

In [ ]:
class KNNClassifier:
    # k: nombre de voisins à regarder
    def __init__(self, k, X_train, Y_train):
        self.k = k
        self.X_train = X_train
        self.Y_train = Y_train
        
    def predict(self, x):
        assert len(x.shape) == 1
        assert x.shape[0] == self.X_train.shape[1]
        
        # TODO TODO
    
    def accuracy(self, X, Y):
        assert len(X.shape) == 2
        assert len(Y.shape) == 1
        assert X.shape[1] == self.X_train.shape[1]
        assert X.shape[0] == Y.shape[0]
        
        # TODO TODO

In [ ]:
for k in range(1, 6):
    classifier = KNNClassifier(k, X_train, Y_train)
    print(k)
    print("Test: ", classifier.accuracy(X_test, Y_test))
    print("Test: ", classifier.accuracy(X_train, Y_train))
    print()

# Classificateur représentants moyens

Dans ce dernier classificateur, plutôt que de garder en mêmoire toutes les données d'entraînement, nous calculons "l'image moyenne" de chaque classe et utilisons celle ci pour prédire le chiffre sur une nouvelle image (c'est-à-dire que pour une image donnée en entrée, la prédiction est le chiffre sur l'image "moyenne" la plus proche).

Qu'observez vous expérimentalement?

In [ ]:
class MeanClassifier:
    def __init__(self, n_classes, X_train, Y_train):
        # matrice qui contiendra le représentant de chaque classe
        self.mean = np.zeros((n_classes, X_train.shape[1]))
        
        # TODO : calculer le représentant de chaque classe
        for c in range(n_classes):
            vecs = X_train[Y_train == c]
            if len(vecs) == 0:
                raise RuntimeError()
            self.mean[c] = np.mean(vecs, axis=0)
        
    def predict(self, x):
        assert len(x.shape) == 1
        
        # cherche le représentant le plus proche et retourne le chiffre correspondant
        # TODO TODO
    
    def accuracy(self, X, Y):
        assert len(X.shape) == 2
        assert len(Y.shape) == 1
        assert X.shape[1] == self.mean.shape[1]
        assert X.shape[0] == Y.shape[0]
        
        # TODO TODO

In [ ]:
classifier = MeanClassifier(10, X_train, Y_train)
print(classifier.accuracy(X_test, Y_test))
print(classifier.accuracy(X_train, Y_train))

Vous pouvez faire une seconde version où la version predict prends une matrice de données et prédit tous les labels, sans faire une seule boucle for! (à garder pour la fin, après l'exercice sur la régression)

In [ ]:
class BatchedMeanClassifier:
    def __init__(self, n_classes, X_train, Y_train):
        self.mean = np.zeros((n_classes, X_train.shape[1]))
        for c in range(n_classes):
            vecs = X_train[Y_train == c]
            if len(vecs) == 0:
                raise RuntimeError()
            self.mean[c] = np.mean(vecs, axis=0)
        
    def predict(self, X):
        assert len(X.shape) == 2
        assert X.shape[1] == self.mean.shape[1]
        
        # TODO TODO
    
    def accuracy(self, X, Y):
        assert len(Y.shape) == 1
        assert Y.shape[0] == X.shape[0]

        return (self.predict(X) == Y).mean()

In [ ]:
classifier = BatchedMeanClassifier(10, X_train, Y_train)
print(classifier.accuracy(X_test, Y_test))
print(classifier.accuracy(X_train, Y_train))

# Régression avec un modèle k plus proches voisins

Dans cette dernière partie, nous nous intéressons à un modèle de prédiction.
Dans ce cas, lorsque vous récupérez les k plus proches voisins, la prédiction est la moyenne de leur sortie.

Nous utilisons pour ça un jeu de donné dont les entrées sont des vitesses d'un véhicule et la sortie la distance nécessaire pour le freinage.

In [ ]:
# read data
def read_speed_and_dist(path):
    x = list()
    y = list()
    with open(path) as instream:
        next(instream)
        for line in instream:
            line = line.strip()
            if len(line) > 0:
                line = line.split(",")
                x.append(float(line[1]))
                y.append(float(line[2]))
    ret_X = np.array(x).reshape(len(x), 1)
    ret_y = np.array(y)
    
    return ret_X, ret_y

X, y = read_speed_and_dist("Speed_and_Stopping_Distances_of_Cars_357_90.csv")
X.shape, y.shape

In [ ]:
# affichage des données
plt.scatter(X[:, 0], y)

In [ ]:
class KNNRegression:
    # k: nombre de voisins à regarder
    def __init__(self, k, X_train, Y_train):
        self.k = k
        self.X_train = X_train
        self.Y_train = Y_train
        
    def predict(self, x):
        assert len(x.shape) == 1
        assert x.shape[0] == self.X_train.shape[1]
        
        # TODO
    

Afficher à la fois les données et les prédictions pour des entrées entre 0 et 25 (utiliser np.linspace).
Qu'observez vous ? Obtendrais-t-on le même genre de prédiction avec un modèle linéaire ?